Test Notebook

In [1]:
import os

import torch
from pathlib import Path
from model import UNET, Separator
from IPython.display import Audio

In [2]:
model_dir = Path('./models')
model_name = 'my_checkpoint_9.pth'
model_file = model_dir / model_name
checkpoint = torch.load(model_name, weights_only=True)

In [3]:
model = UNET()
model.load_state_dict(checkpoint['state_dict'])
model.eval()

RuntimeError: Error(s) in loading state_dict for UNET:
	Unexpected key(s) in state_dict: "ups.1.residual.weight", "ups.1.residual.bias", "ups.3.residual.weight", "ups.3.residual.bias", "ups.5.residual.weight", "ups.5.residual.bias", "ups.7.residual.weight", "ups.7.residual.bias", "downs.0.residual.weight", "downs.0.residual.bias", "downs.1.residual.weight", "downs.1.residual.bias", "downs.2.residual.weight", "downs.2.residual.bias", "downs.3.residual.weight", "downs.3.residual.bias", "bottleneck.residual.weight", "bottleneck.residual.bias". 

In [5]:
import musdb

musdb_testdata = musdb.DB('./musdb', download=False, subsets='test')

In [6]:
track = musdb_testdata[0]
mix_audio = torch.as_tensor(track.audio.T, dtype=torch.float32)
vocal_audio = torch.as_tensor(track.targets['vocals'].audio.T, dtype=torch.float32)

In [36]:
sep = Separator(n_fft=1024, hop_length=512, model=model, device='cuda')

vocal_prediction = sep(mix_audio.unsqueeze(0))

In [38]:
Audio(mix_audio, rate=44100)

In [39]:
Audio(vocal_prediction[0].cpu(), rate=44100)

In [ ]:
import museval

def estimate_and_evaluate(vocal_audio):
    # assume mix as estimates
    estimates = {
        'vocals': track.audio,
    }

    # Evaluate using museval
    scores = museval.eval_mus_track(
        track, estimates, output_dir="path/to/json"
    )

    # print nicely formatted and aggregated scores
    print(scores)

Load From Numpy File

In [18]:
import numpy as np

pred_batch = np.load('./saved_spectrograms/9/predbatch_50.npy')
pred_batch.shape

(4, 2, 513, 585)

In [19]:
pred = torch.from_numpy(pred_batch[0]).to('cuda')
pred

tensor([[[ 14.7338,  29.2177,  35.6677,  ...,  24.3456,  21.6779,  11.2504],
         [ 21.8633,  99.1884,  48.8659,  ...,  13.6795,  18.4752,  14.4105],
         [ 44.1165, 114.3330,  41.4519,  ...,   8.5746,  15.1726,   9.3708],
         ...,
         [ 10.8124,  16.8460,   3.9047,  ...,   5.6080,  11.7985,  15.0673],
         [ 13.6480,  12.8197,   5.9257,  ...,   5.4478,  10.7333,  18.3148],
         [ 47.1708,  33.7250,  12.0922,  ...,  27.8579,  48.7999,  78.4530]],

        [[ 19.2083,  33.2332,  29.2780,  ...,  19.9170,  27.6634,   8.4732],
         [ 20.4255,  90.1030,  35.4981,  ...,   9.6559,  16.6567,   9.0220],
         [ 30.6450,  79.9417,  38.0503,  ...,   7.8981,  11.0415,   7.4333],
         ...,
         [  7.9184,  10.6870,   3.2105,  ...,   4.5145,   8.0386,   9.9369],
         [ 14.1335,  11.1933,   4.4373,  ...,   4.1827,   9.1163,  13.4977],
         [ 37.6363,  23.9491,  10.8809,  ...,  24.8503,  34.8660,  61.5477]]],
       device='cuda:0')

In [20]:
from transforms import make_filterbanks

stft, istft = make_filterbanks(
            n_fft=1024,
            hop_length=512,
            center=False,
            sample_rate=44100.0,
            device='cuda'
        )

In [21]:
pred_audio = istft(pred)
pred_audio.shape

torch.Size([2, 299008])

In [22]:
from IPython.display import Audio

Audio(pred_audio.cpu(), rate=44100)

Testing Train Dataset

In [9]:
from dataset import MUSDBDataset

train_dataset = MUSDBDataset('./musdb')

train_dataset.shape

(tensor([[ 0.0292,  0.0267,  0.0082,  ..., -0.0131, -0.0286, -0.0517],
         [ 0.0468,  0.0305,  0.0042,  ..., -0.1584, -0.1554, -0.1486]]),
 tensor([[-0.0260, -0.0229, -0.0198,  ..., -0.0267, -0.0140, -0.0039],
         [ 0.0040,  0.0041,  0.0042,  ..., -0.0243, -0.0056,  0.0082]]))

In [19]:
audio, vocal = train_dataset[71]

In [20]:
Audio(audio, rate=44100)

In [21]:
Audio(vocal, rate=44100)